<a href="https://colab.research.google.com/github/nitsundon/100DaysofML/blob/main/Day1/RNN.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [13]:
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
import plotly.express as px

In [2]:
df= pd.read_pickle("/content/drive/MyDrive/Libraries/pickle/preprocessed_demand_df.pkl")

In [12]:
df1=df.interpolate().set_index('datetime')
scaler = MinMaxScaler()
data_scaled = scaler.fit_transform(df1)
data_scaled_df = pd.DataFrame(data_scaled, columns=df1.columns, index=df1.index)
data_scaled_df.head()

demand
datetime                     
2022-01-01 00:00:00  0.326487
2022-01-01 00:15:00  0.325481
2022-01-01 00:30:00  0.320685
2022-01-01 00:45:00  0.327153
2022-01-01 01:00:00  0.328219

In [16]:
fig = px.line(data_scaled_df,  y=["demand"],
              title="State Demand Over Time (15-Min Blocks)",
              labels={"Timestamp": "Time", "Demand_MW": "Demand (MW)"},
              template="simple_white")  # Optional: Use "seaborn" or "simple_white" theme

# Show interactive graph
fig.show()

In [17]:
def create_sequences(data, seq_length):
    x, y = [], []
    for i in range(len(data) - seq_length):
        x.append(data[i:i+seq_length])
        y.append(data[i+seq_length])
    return np.array(x), np.array(y)

In [26]:
import numpy as np
seq_length = 24  # assuming hourly data, this uses past 24 hours
X, y = create_sequences(data_scaled[-(96*365*2):], seq_length)
X,y

(array([[[0.69314444],
         [0.70032421],
         [0.70992376],
         ...,
         [0.62970137],
         [0.6261322 ],
         [0.63090885]],
 
        [[0.70032421],
         [0.70992376],
         [0.70850431],
         ...,
         [0.6261322 ],
         [0.63090885],
         [0.64306357]],
 
        [[0.70992376],
         [0.70850431],
         [0.7164487 ],
         ...,
         [0.63090885],
         [0.64306357],
         [0.63535996]],
 
        ...,
 
        [[0.78725186],
         [0.78008702],
         [0.75990438],
         ...,
         [0.84853913],
         [0.84939387],
         [0.84394343]],
 
        [[0.78008702],
         [0.75990438],
         [0.75896103],
         ...,
         [0.84939387],
         [0.84394343],
         [0.83846199]],
 
        [[0.75990438],
         [0.75896103],
         [0.75555944],
         ...,
         [0.84394343],
         [0.83846199],
         [0.8426024 ]]]),
 array([[0.64306357],
        [0.63535996],
        [0.

In [27]:
split = int(0.8 * len(X))
X_train, X_test = X[:split], X[split:]
y_train, y_test = y[:split], y[split:]


In [28]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import SimpleRNN, Dense
from sklearn.preprocessing import MinMaxScaler
# Define the RNN model
model = Sequential()
model.add(SimpleRNN(50, activation='relu', input_shape=(seq_length, 1)))
model.add(Dense(1))
model.compile(optimizer='adam', loss='mse')

/usr/local/lib/python3.11/dist-packages/keras/src/layers/rnn/rnn.py:200: UserWarning:

Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.



In [29]:
model.fit(X_train, y_train, epochs=20, batch_size=16, validation_data=(X_test, y_test))


Epoch 1/20
3503/3503 ━━━━━━━━━━━━━━━━━━━━ 26s 7ms/step - loss: 0.0076 - val_loss: 1.8377e-04
Epoch 2/20
3503/3503 ━━━━━━━━━━━━━━━━━━━━ 41s 7ms/step - loss: 1.3413e-04 - val_loss: 1.0111e-04
Epoch 3/20
3503/3503 ━━━━━━━━━━━━━━━━━━━━ 41s 7ms/step - loss: 8.8255e-05 - val_loss: 1.1472e-04
Epoch 4/20
3503/3503 ━━━━━━━━━━━━━━━━━━━━ 24s 7ms/step - loss: 7.8174e-05 - val_loss: 7.5154e-05
Epoch 5/20
3503/3503 ━━━━━━━━━━━━━━━━━━━━ 41s 7ms/step - loss: 7.1741e-05 - val_loss: 1.3114e-04
Epoch 6/20
3503/3503 ━━━━━━━━━━━━━━━━━━━━ 40s 7ms/step - loss: 6.7600e-05 - val_loss: 1.0884e-04
Epoch 7/20
3503/3503 ━━━━━━━━━━━━━━━━━━━━ 26s 8ms/step - loss: 6.7698e-05 - val_loss: 7.9183e-05
Epoch 8/20
3503/3503 ━━━━━━━━━━━━━━━━━━━━ 23s 7ms/step - loss: 6.5029e-05 - val_loss: 7.1938e-05
Epoch 9/20
3503/3503 ━━━━━━━━━━━━━━━━━━━━ 24s 7ms/step - loss: 6.7365e-05 - val_loss: 8.4932e-05
Epoch 10/20
3503/3503 ━━━━━━━━━━━━━━━━━━━━ 40s 6ms/step - loss: 6.8654e-05 - val_loss: 7.8050e-05
Epoch 11/20
3503/3503 ━━━━━━━━━━━